---
## Abstract
##### La décote littorale représente la dépréciation des valeurs immobilières liées aux risques cotiers (montée des eaux, submersion, érosion). A partir des transactions recensées par DVF en 2023 et de l'application Géorisques, nous construisons un modèle hédonique et spatial pour évaluer l'effet causal de la présence en zone inondable. Selon ce modèle, les appartements exposés ubiraient une décote de près de 5%, tandis que les transactions liées aux maisons resteraient insensibles, ce qui traduirait un effet de myopie persistant des achats des particuliers
---

## Sommaire

1. [Introduction : la décloôte littorale](#1-introduction--la-decote-littorale)
2. [Initialisation : installation et import des modules](#2-initialisation--installation-et-import-des-modules)
3. [Les communes côtières](#3-les-communes-cotieres)
4. [Les transactions cotières](#4-les-transactions-cotieres)
5. [Localiser les zones inondables](#5-localiser-les-zones-inondables)
6. [Visualisation](#6-visualisation)
7. [Modèle économétrique](#7-modele-econometrique)

---
# 1. Introduction : la décote littorale

Selon l'INRAE, 20% de la population mondiale vit à moins de 30 km des côtes. Cette population est donc particulièrement exposée aux risques associés au changement climatique. France Stratégie (Robinet & Delahais, 2023) et l'ADEME (Jacquetin & Callonnec, 2024) recensent notamment les risques cotiers suivants :
- la montée du niveau de la mer
- les risques de submersion marine
- les risques de submersion fluviale, en particulier dans les communes à l'embouchure des fleuves

Si la montée du niveau de la mer est un risque dit "chronique" (i.e. il se matérialise progressivement sur le long terme), les risques de submersion sont considérés comme des risques aigus (aléas soudains aux conséquences imprévisibles) et peuvent conduire, en France, à la reconnaissance par l'Etat d'une situation de catastrophe naturelle. Par exemple, en 2010, la tempête Xynthia a frappé le littoral atlantique et les digues ont cédé dans plusieurs zones, notamment en Vendée et Charente-Maritime. Sur le long terme, par la seule montée du trait de côte près d'un millier de bâtiments, pour une valeur de 235 M€, pourraient être touchés à horizon 2028 (CEREMA, 2024)

En plus des dégâts matériels et humains, ces risques modifient fortement les dynamiques économiques locales. En particulier, le secteur immobilier est particulièrement exposé à ces risques : évolution de la demande mais aussi sur la valorisation des actifs exposés. Cela fait peser des risques sur le patrimoine des propriétaires (ménages, investisseurs) mais aussi sur les acteurs financiers qui financent ces acquisitions. L'INRAE (2023) estime par exemple que les prix en zone inondable seraient plus bas de 10 à 21 % par rapport à des biens similaires à proximité.

Nous nous proposons d'évaluer le __*discount climatique*__, c'est-à-dire la dévalorisation d'un bien immobilier associée à la prise en compte du risque climatique. Nous utiliserons notamment la base DVF (Demande de Valeurs Foncières), les API de géolocalisation (OverPass, API Adresse) et l'API de localisation des risques inondation Géoriques, qui recense les localisations dans TRI (territoires à Risques importants d'Inondation). Enfin, nous utilisons les bases de données cadastrales pour identifier les caractéristiques immobilières des parcelles.

Par un modèle à la fois hédonique (la valeur d'un bien dépend de ses caractéristiques spécifiques) et géographique (cette valeur dépend de sa situation géographique dans la commune), nous confirmons l'existence de ce discount (__*5% en moyenne pour les transactions d'appartements*__), mais cette valeur moyenne cache d'importantes hétérogénéités et surtout dépend du type d'acquisition et du type de risque associé.

---
# 2. Initialisation : installation et import des modules
[Retour au sommaire](#sommaire)

In [1]:
## La version de python utilisée est 3.12.8

!pip install -r requirements.txt -q

In [104]:
from concurrent.futures import ThreadPoolExecutor
from IPython.display import display
import pandas as pd
import numpy as np
import requests
import lxml as lxml
import io as io
import os
import geopandas as gpd
import overpy
import ast

from script import process_data
from script import geolocaliser
from script import request_tri
from script import process_data
from script import mapping
from script import modeling
from script import process_dvf

In [3]:
# Pour faciliter la lecture
import warnings
warnings.filterwarnings("ignore")

---
# 3. Les communes cotieres
[Retour au sommaire](#sommaire)

On crée le geodataframe des communes cotières.

In [4]:
shapefile_path = "data/communes_cotieres/communes_cotieres.shp"

df_cotieres = gpd.read_file(shapefile_path)

df_cotieres = df_cotieres[['code', 'nom', 'NumDep']].drop_duplicates(subset='nom').sort_values(by='nom').reset_index(drop=True)

On répertorie les communes dans une liste (pour filtrer les cartes suivantes).

In [5]:
liste_cotieres = df_cotieres['nom'].unique().tolist()

On associe les départements et les régions à chaque commune.

In [6]:
df_cotieres = df_cotieres.rename(columns={
    'nom': 'Nom commune',
    'code': 'code_commune',
    'NumDep': 'departement'
})

region = pd.read_csv('data/code_region.csv',encoding="utf8",sep=";")

df_cotieres['departement'] = df_cotieres['departement'].astype(str).astype(int)

df_cotieres = df_cotieres.merge(
    region,  # DataFrame region utilisé pour la fusion
    left_on='departement', 
    right_on='departmentCode',  # Colonne correspondante dans region
    how='left'  # Fusion de type left join
)

On renseigne les populations à partir des bases de recensement.

In [7]:
url = "https://www.insee.fr/fr/statistiques/fichier/7739582/ensemble.zip"
df_population = process_data.process_population_data(url)
print(df_population.head())

  code_commune  Population
0        01001         832
1        01002         267
2        01004       14854
3        01005        1897
4        01006         113


In [8]:
df_cotieres = df_cotieres.merge(df_population,left_on='code_commune',right_on='code_commune')

On calcule des statistiques descriptives sur les populations cotières, par région

In [9]:
stats_region_filtered = df_cotieres.groupby('regionName').apply(
    lambda x: pd.Series({
        'nombre_communes': x['Nom commune'].nunique(),
        'population_totale': x['Population'].sum()  # Décommente si la colonne 'Population' existe
    })
).reset_index()

# Afficher les résultats
tableau_communes = stats_region_filtered.sort_values(by='nombre_communes', ascending=False).fillna("").style.hide(axis="index")

# Afficher le tableau sans NaN et sans index
tableau_communes

In [10]:
# Calcul des statistiques par commune
stats_communes = df_cotieres.groupby('Nom commune').apply(
    lambda x: pd.Series({
        'Population': x['Population'].sum()  # Décommente si la colonne 'Population' existe
    })
).reset_index()

top_20_communes = (
    stats_communes
    .sort_values(by='Population', ascending=False)
    .head(20)
    .style.hide(axis="index")
    .format({'Population': lambda x: f"{x:,.0f}".replace(',', ' ')})  # Remplacement de la virgule par un espace
)

display(top_20_communes)

In [11]:
# Charger le fichier GeoJSON des communes de France depuis le lien GitHub
url_commune = 'https://raw.githubusercontent.com/gregoiredavid/france-geojson/master/communes.geojson'
response_commune = requests.get(url_commune)
communes_geojson = response_commune.json()

# Charger le GeoJSON dans un GeoDataFrame
gdf_communes = gpd.GeoDataFrame.from_features(communes_geojson['features'])
gdf_communes_cotieres = gdf_communes[gdf_communes['nom'].isin(liste_cotieres)]
gdf_communes_cotieres = gdf_communes_cotieres.merge(df_cotieres[['Nom commune', 'Population']], 
                                                    left_on='nom', 
                                                    right_on='Nom commune'
                                                    ).drop(columns=['Nom commune'])


In [12]:
# Calculer les centroïdes pour chaque commune
gdf_communes_cotieres['centroid'] = gdf_communes_cotieres.geometry.centroid
gdf_communes_cotieres['latitude_centre'] = gdf_communes_cotieres['centroid'].y
gdf_communes_cotieres['longitude_centre'] = gdf_communes_cotieres['centroid'].x
gdf_communes_cotieres = gdf_communes_cotieres.drop(columns=['centroid'])

liste_commune = gdf_communes_cotieres['nom'].to_list()

On utilise l'API Overpass (module *overpy*) pour successivement géolocaliser les mairies, les stations de transport et les plages de la commune.

Cette API repose sur les 3 structures suivantes :

- Un *node* est un point géographique défini par des coordonnées de latitude et de longitude.
- Un *way* est une séquence de nodes qui forment une ligne ou une zone. Les ways peuvent être utilisés pour représenter des objets linéaires (routes, rivières) ou des zones fermées (bâtiments, parcs, lacs).
- Une *relation* est un groupe de nodes, ways et d'autres relations qui sont regroupés pour définir des objets plus complexes

In [13]:
# Appliquer la fonction sur chaque commune
api = overpy.Overpass()

Exemple de requête d'Overpass : la mairie de Cannes. On cherche exclusivement des nodes (amenity = townhall)

In [14]:
query = f"""
[out:json];
area[name="Cannes"]->.searchArea;
node["amenity"="townhall"](area.searchArea);
out body;
"""
# Exécuter la requête
result = api.query(query)
print(result.nodes)

[<overpy.Node id=1688895428 lat=43.5491403 lon=6.9815001>]


Ici il n'y a qu'un résultat. Parfois il y en a plusieurs, on sélectionne alors le premier.

On réalise cette recherche pour toutes les communes cotières.

In [15]:
gdf_communes_cotieres[['latitude_mairie', 'longitude_mairie']] = gdf_communes_cotieres.apply(
    lambda row: pd.Series(geolocaliser.get_townhall_coordinates(row['nom'], api)),
    axis=1
)

Dans le cas où Overpass ne permet pas de géolocaliser la mairie, on fait une recherche par mot-clé à partir de l'API Adresse de l'Institut National Géographique (https://adresse.data.gouv.fr/api-doc/adresse)

In [16]:
# Liste des mots-clés pour localiser les mairies
mots_cles = [
    "Mairie+de", 
    "Hotel+de+ville+de", 
    "Bureau+du+Maire+de", 
    "Salle+des+Fêtes+de", 
    "Maison+Communale+de", 
    "Centre+Administratif+de", 
    "Hôtel+de+Ville", 
    "Bâtiment+Municipal+de", 
    "Mairie+municipale+de", 
    "Maison+des+Services+de"
]

# Compléter les coordonnées manquantes
gdf_communes_cotieres = geolocaliser.geolocaliser_mot_cle(
    gdf_communes_cotieres, 
    colonne_commune='nom', 
    colonne_geometry='geometry', 
    mots_cles=mots_cles, 
    colonne_latitude='latitude_mairie', 
    colonne_longitude='longitude_mairie'
    )

Et on procède de même pour tous les autres lieux importants : plages, port, stations de transport

In [17]:
# Pour les plages
gdf_communes_cotieres['beach_coordinates'] = gdf_communes_cotieres.apply(
    lambda row: geolocaliser.get_beach_coordinates(row['nom'], api),
    axis=1
    )

# Liste des mots-clés pour localiser les plages
mots_cles_plages = [ 
    "Plage+de",
    "Plage",
    "Beach"
    ]

# Compléter les coordonnées manquantes pour les plages
gdf_communes_cotieres = geolocaliser.geolocaliser_mot_cle(
    gdf_communes_cotieres, 
    colonne_commune='nom', 
    colonne_geometry='geometry', 
    mots_cles=mots_cles_plages, 
    colonne_latitude='latitude_plage', 
    colonne_longitude='longitude_plage'
    )

In [18]:
# Pour les stations de transport
gdf_communes_cotieres['station'] = gdf_communes_cotieres.apply(
    lambda row: geolocaliser.get_station_coordinates(row['nom'], api),
    axis=1
    )

# Liste des mots-clés pour localiser les gares
mots_cles_gares = [ 
    "Gare+de"
    ]

# Compléter les coordonnées manquantes pour les gares
gdf_communes_cotieres = geolocaliser.geolocaliser_mot_cle(
    gdf_communes_cotieres, 
    colonne_commune='nom', 
    colonne_geometry='geometry', 
    mots_cles=mots_cles_gares, 
    colonne_latitude='latitude_gare', 
    colonne_longitude='longitude_gare'
    )

In [19]:
# Pour les ports
gdf_communes_cotieres[['latitude_port', 'longitude_port']] = gdf_communes_cotieres.apply(
    lambda row: pd.Series(geolocaliser.get_ports(row['nom'],
                                                 api)
                          ),
    axis=1
    )

# Liste des mots-clés pour localiser les ports
mots_cles_ports = [ 
    "Port+de",
]

# Compléter les coordonnées manquantes pour les ports
gdf_communes_cotieres = geolocaliser.geolocaliser_mot_cle(
    gdf_communes_cotieres, 
    colonne_commune='nom', 
    colonne_geometry='geometry', 
    mots_cles=mots_cles_ports, 
    colonne_latitude='latitude_port', 
    colonne_longitude='longitude_port'
)

Pour les stations et les plages, qui peuvent être nombreux pour une seule commune, on retient des listes exhaustives de coordonnées, puis on les convertit en tuples.

In [20]:
# Application
gdf_communes_cotieres['station'] = gdf_communes_cotieres['station'].apply(process_data.fix_coordinates_format)
gdf_communes_cotieres['beach_coordinates'] = gdf_communes_cotieres['beach_coordinates'].apply(process_data.fix_coordinates_format)

Si on ne trouve pas de plage, le ports est ajouté à cette liste. En effet, la présence d'un port capte également un effet positif lié à la proximité de l'habitation à la mer.

In [21]:
gdf_communes_cotieres["beach_coordinates"] = gdf_communes_cotieres.apply(
    lambda row: row["beach_coordinates"] + [(row["latitude_plage"], row["longitude_plage"])] if row["latitude_plage"] is not None and row["longitude_plage"] is not None else row["beach_coordinates"],
    axis=1
    )

On supprime les premières coordonnées trouvées sur OverPass (une fois ajoutées à la liste)

In [22]:
gdf_communes_cotieres = gdf_communes_cotieres.drop(columns=['latitude_plage',
                                                            'longitude_plage',
                                                            'latitude_gare',
                                                            'longitude_gare','code'
                                                            ]
                                                   )

On résume ici la complétude du renseignement de ces informations :
- on recense des plages et des stations pour toutes les communes
- une mairie est localisée dans 9 communes sur 10
- un port est localisé dans 6 communes sur 10

In [23]:
# Calcul de la part de chaque variable renseignée
summary = {
    "Variable": gdf_communes_cotieres.columns,
    "Part (%)": [
        gdf_communes_cotieres[col].notnull().mean() * 100 
        for col in gdf_communes_cotieres.columns
        ]
    }

# Création d'un DataFrame pour présentation
summary_df = pd.DataFrame(summary)

# Filtrer uniquement les colonnes désirées
columns_to_display = [
    "geometry",
    "Population",
    "latitude_mairie", 
    "beach_coordinates",
    "station",
    "latitude_port"
    ]

filtered_summary_df = summary_df[summary_df["Variable"].isin(columns_to_display)]

# Style pour affichage dans le notebook
styled_table = (
    filtered_summary_df.style
    .hide(axis="index")  # Cache l'index
    .set_caption("Part de variables renseignées")
    .format({"Part (%)": "{:.1f}%"})  # Formate les pourcentages
)

# Affichage dans le notebook
display(styled_table)

Enregistrement de la base intermédiaire de la partie 1 _*. data/communes_cotieres.csv*_ qui contient :
- la liste des communes cotières (nom et numéro)
- le département et la région associée
- la population recensée
- les coordonnées des principaux lieux (mairie, port, plages(s), station(s))

In [24]:
gdf_communes_cotieres.to_csv('data/communes_cotieres.csv',
                             encoding="utf8",
                             sep=";",
                             index=False
                             )

---
# 4. Les transactions cotieres
[Retour au sommaire](#sommaire)

On télécharge la base Demande de valeurs foncières (DVF) qui référence, pour l'année 2023, l'ensemble des mutations à titre onéreux (en majeure partie géolocalisées) : https://files.data.gouv.fr/geo-dvf/latest/csv/2023/full.csv.gz

Les informations sont issues de la Base nationale des données patrimoniales, alimentées par le système d'information de la DGFip et couvrent la France métropolitaine à l'exception des départements du Bas-Rhin, du Haut-Rhin et de Moselle.

La base recense des actes (id_mutation), qui comportent une ou plusieurs mutations distinctes, repérées par le numéro de disposition (numero_disposition).

Les observations de la base, appelées "lignes de restitution", concernent les différents locaux d'une mutation (Appartement, Maison, Dépendance, Local Industriel), ventilées selon autant de natures de culture présentes dans l'immeuble.

In [25]:
url = "https://files.data.gouv.fr/geo-dvf/latest/csv/2023/full.csv.gz"
output_csv_path = "full.csv"

process_data.download_and_extract_csv(url,
                                      output_csv_path
                                      )

# Charger directement le fichier CSV dans un DataFrame
df = pd.read_csv(output_csv_path,
                 encoding="utf-8"
                 )

os.remove(output_csv_path)

On allège le fichier des transactions.

In [26]:
colonnes_a_supprimer = ['adresse_suffixe',
                        'code_nature_culture',
                        'ancien_code_commune',
                        'ancien_nom_commune',
                        'ancien_id_parcelle',
                        'numero_volume',
                        'code_nature_culture_speciale',
                        'nature_culture_speciale',
                        'lot1_numero',
                        'lot2_numero',
                        'lot3_numero',
                        'lot4_numero',
                        'lot5_numero',
                        'lot1_surface_carrez',
                        'lot2_surface_carrez',
                        'lot3_surface_carrez',
                        'lot4_surface_carrez',
                        'lot5_surface_carrez'
                        ]

df.drop(columns=colonnes_a_supprimer, inplace=True)

On affiche un extrait de la base ainsi téléchargée

In [ ]:
display(df.head())

Les données présentes dans le fichier sont les suivantes :

- *Identifiant de mutation / Numéro de disposition* : Chaque couple est un identifiant unique d'un acte de vente

- *Nature de la mutation* : Il s'agit du type de vente qui a eu lieu. Il peut s'agir d'une vente classique, d'une vente en l’état futur d’achèvement, d'une vente de terrain à bâtir, d'une adjudication, ou d'une expropriation ou échange.

- *Valeur foncière* : Montant de la vente. Il est TTC et n'inclut pas les frais de notaire et les éventuels frais d'agence.

- *Adresse* : L'adresse exacte du bien est communiquée via plusieurs colonnes comme le numéro de voie, le code postal etc.

- *Latitude/Longitude* : Remplies de manière presque exhaustive.

- *Informations cadastrales* : Des informations cadastrales sont fournies telles que l'identifiant de parcelle.

- *Nombre de lots* (restitués jusqu'à 5)

- *Type de local*: Il peut s'agir d'une maison, d'un appartement, d'une dépendance (isolée), ou d'un local industriel et commercial ou assimilés.

- *Surface réelle bâti*, mesurée au sol entre les murs, différente de la surface Carrez.

- *Nombre de pièces principales* du bien immobilier

- *Nature culture* : Pour les terrains une nature de culture est renseignée afin de connaître son utilisation. Les types de terrains possible sont : terrains a bâtir, terrains d'agrément, bois, futaies feuillues, futaies mixtes, oseraies, peupleraies, futaies résineuses, taillis sous futaie, taillis simples, carrières, chemin de fer, eaux, jardins, landes, landes boisées, prés, pâtures, pacages, prés d'embouche, herbages, prés plantes, sols, terres, terres plantées, vergers, vignes

- Surface Terrain: Surface cadastrale du terrain.

On reprend le fichier des communes cotières et on ne retient dans DVF que les transactions liées à ces communes

In [27]:
df_cotieres = pd.read_csv('data/communes_cotieres.csv',sep=";")
df_cotieres = df_cotieres.rename(columns={'latitude': 'latitude_centre'})
df_cotieres = df_cotieres.rename(columns={'longitude': 'longitude_centre'})

liste_cotieres = sorted(df_cotieres['nom'].unique().tolist())

1er filtre : On restreint DVF aux seules communes côtières.

In [28]:
pourcentage_supprime = 100 - (len(df[df['nom_commune'].isin(liste_cotieres)]) / len(df) * 100)
print(f"{pourcentage_supprime:.2f}% des lignes sont supprimées après le filtrage des communes littorales.")
df = df[df['nom_commune'].isin(liste_cotieres)]

88.07% des lignes sont supprimées après le filtrage des communes littorales.


2ème filtre : on ne retient que les ventes.

In [29]:
pourcentage_supprime = 100 - (len(df[df['nature_mutation'] == 'Vente']) / len(df) * 100)
print(f"{pourcentage_supprime:.2f}% des lignes sont supprimées après le filtrage sur 'Vente'.")
df = df[df['nature_mutation'] == 'Vente']
df = df.drop(columns=['nature_mutation'])

8.31% des lignes sont supprimées après le filtrage sur 'Vente'.


3ème filtre : On ne retient que les mutations dont la valeur foncière est renseignée

In [30]:
pourcentage_conserve = len(df[df['valeur_fonciere'] > 0]) / len(df) * 100
print(f"{pourcentage_conserve:.2f}% des lignes sont conservées après le filtre.")
df = df[df['valeur_fonciere'] > 0]

99.31% des lignes sont conservées après le filtre.


In [31]:
print(df.shape[0])
print(df['id_mutation'].unique().shape[0])

412848
179496


In [32]:
# Fonction pour afficher le tableau filtré dans un joli format pour Jupyter Notebook
def afficher_tableau_par_id_mutation(df, id_mutation_str):
    # Filtrer le DataFrame en fonction de l'id_mutation
    df_filtered = df[df['id_mutation'].astype(str) == id_mutation_str]
    
    # Sélectionner les colonnes nécessaires
    df_filtered = df_filtered[['id_mutation', 'valeur_fonciere', 'type_local', 'surface_reelle_bati', 'surface_terrain','nature_culture', 'nombre_pieces_principales']]
    
    # Affichage du tableau joli avec pandas pour Jupyter Notebook
    display(df_filtered)


Cas le plus typique : un seul local dans une seule mutation

In [33]:
# Exemple d'utilisation
afficher_tableau_par_id_mutation(df, '2023-457573')

id_mutation  valeur_fonciere   type_local  surface_reelle_bati  \
1330716  2023-457573          85600.0  Appartement                 55.0   

         surface_terrain nature_culture  nombre_pieces_principales  
1330716              NaN            NaN                        3.0

Cas n°2 : Plusieurs locaux dans une mutation. Dans ce cas, il faut identifier si la mutation concerne une maison, un appartement, ou autre chose.

In [34]:
afficher_tableau_par_id_mutation(df, '2023-457574')

id_mutation  valeur_fonciere   type_local  surface_reelle_bati  \
1330717  2023-457574         230000.0  Appartement                 22.0   
1330718  2023-457574         230000.0   Dépendance                  NaN   

         surface_terrain nature_culture  nombre_pieces_principales  
1330717              NaN            NaN                        1.0  
1330718              NaN            NaN                        0.0

Cas n°3 : Quand une disposition comporte plusieurs locaux ou plusieurs natures de culture, le fichier de restitution comporte autant de lignes qu’il y a de locaux ou de nature de culture concernés par la mutation.
Ainsi, pour une même publication, il peut y avoir 1 à n ligne(s) de restitution. Les données génériques (ainsi que le prix) sont alors répétées sur chaque ligne.
On retire d abord les nature_culture autre que "sols" puis on repère le type de local principal

In [35]:
afficher_tableau_par_id_mutation(df, '2023-457957')

id_mutation  valeur_fonciere  type_local  surface_reelle_bati  \
1331555  2023-457957         539000.0  Dépendance                  NaN   
1331556  2023-457957         539000.0      Maison                111.0   
1331557  2023-457957         539000.0      Maison                111.0   
1331558  2023-457957         539000.0  Dépendance                  NaN   

         surface_terrain       nature_culture  nombre_pieces_principales  
1331555            280.0  terrains d'agrément                        0.0  
1331556            280.0  terrains d'agrément                        4.0  
1331557            750.0                 sols                        4.0  
1331558            750.0                 sols                        0.0

On ne retient que les surfaces d'habitation, donc celles avec nature_culture vide ou égale à sols.

In [36]:
df = df[df['nature_culture'].isna() | (df['nature_culture'] == 'sols')]

In [37]:
# Appliquer le traitement avec le groupement par plusieurs colonnes
df = df.groupby(['id_mutation', 'numero_disposition']).apply(process_dvf.process_group)

# Réinitialiser l'index
df.reset_index(drop=True, inplace=True)

On ne retient que les appartements et les maisons

In [38]:
df = df[(df['appart_present'] == True) | (df['maison_present'] == True)]

# Assigner "Appartement" ou "Maison" à la colonne type_local
df['type_local'] = df.apply(
    lambda row: 'Maison' if row['maison_present'] else 'Appartement', axis=1
)

# Supprimer les colonnes appart_present et maison_present
df.drop(columns=['appart_present', 'maison_present'], inplace=True)

In [39]:
df = df[df['surface_reelle_bati'] > 0]
df['prix_m2'] = df['valeur_fonciere'] / df['surface_reelle_bati']

Il reste des doublons. La plupart concernent les exactes mêmes transactions (mais ont des numéros de disposition différentes). Seules quelques unes concernent des dispositions à des adresses différentes. Comme on ne peut pas différencier les prix, on les supprime

In [42]:
# Une partie des transactions sont en doublon
df = df[~df.duplicated(subset=['id_mutation', 'prix_m2'], keep='first')]

df = df[~df.duplicated(subset=['id_mutation'], keep=False)]


In [43]:
colonnes_a_nettoyer = ['adresse_numero', 'code_postal']
df = process_data.nettoyer_colonnes(df, colonnes_a_nettoyer)
# Convertir la colonne 'code_commune' en type string
df['code_commune'] = df['code_commune'].astype('string')

# Ajouter un '0' au début si la chaîne a 4 caractères
df['code_commune'] = [x.zfill(5) if len(x) == 4 else x for x in df['code_commune']]

# Vérifier les résultats
print(df['code_commune'].head())

0    76540
1    76540
2    76157
3    76103
4    76540
Name: code_commune, dtype: object


In [44]:
# 4ème opération (si besoin de géolocalisation) : Compléter par le type de voie

voie = pd.read_csv("data/voie.csv",sep=";",encoding="utf-8")
print(voie.head())

# Liste des abréviations de types de voie
abbreviations = voie['abreviation'].tolist()

# Appliquer la fonction à la colonne 'adresse_nom_voie'
result = [process_data.check_abbreviation(adresse,abbreviations) for adresse in df['adresse_nom_voie']]

# Décomposer les résultats dans les colonnes 'type_voie' et 'nom_voie'
df['type_voie'] = [x[0] for x in result]
df['nom_voie'] = [x[1] for x in result]

df = df.merge(voie,left_on=['type_voie'],right_on=['abreviation'])

  abreviation type_voie_complet
0         RUE               Rue
1          AV            Avenue
2         RTE             Route
3         CHE            Chemin
4          BD         Boulevard


In [45]:
## 5ème : Réécriture de l'adresse
df['Adresse'] = df['adresse_numero'] + ' ' + df['type_voie_complet'] + ' ' + df['nom_voie'] + ' ' + df['code_postal'] + ' ' + df['nom_commune']

display(df['Adresse'].head())

0           48 Rue DE CONSTANTINE 76000 Rouen
1           45 Rue DES CHARRETTES 76000 Rouen
2    14 Boulevard CLAUDE MONET 76380 Canteleu
3        20 Allée DES FLEURS 76240 Bonsecours
4                   35 Rue MUSTEL 76000 Rouen
Name: Adresse, dtype: string

In [46]:
# Charger les données des codes de région
region = pd.read_csv('data/code_region.csv', sep=';')

In [47]:
#Fusionner df_geolocalisees avec les codes de région
df = df.merge(region, left_on=["code_departement"], right_on=['departmentCode'], how='left')

df['regionCode'] = df['regionCode'].astype('Int64')  # Utilise Int64 pour gérer les valeurs manquantes
#Compter le nombre de transactions par région

transactions_par_region = df.groupby('regionName').size()

# Calculer le total des transactions
total_transactions = transactions_par_region.sum()

# Calculer la part de chaque région dans le total des transactions
part_region = (transactions_par_region / total_transactions) * 100

# Créer un DataFrame avec les résultats
tableau_regions = pd.DataFrame({
    'Nombre de transactions': transactions_par_region,
    'Part du total (%)': part_region
})

# Afficher le tableau des régions
display(tableau_regions)

Nombre de transactions  Part du total (%)
regionName                                                           
Auvergne-Rhône-Alpes                           111           0.113960
Bourgogne-Franche-Comté                         43           0.044146
Bretagne                                      7012           7.198957
Centre-Val de Loire                             50           0.051333
Grand Est                                       42           0.043120
Guadeloupe                                       6           0.006160
Hauts-de-France                               6052           6.213361
Normandie                                    13903          14.273688
Nouvelle-Aquitaine                            6471           6.643533
Occitanie                                    16243          16.676078
Pays de la Loire                             13541          13.902036
Provence-Alpes-Côte d'Azur                   33835          34.737123
Île-de-France                                   94           0.096506

3. Calcul de la base des prix au mètre carré

Notre objectif est d'évaluer le prix au mètre carré des biens en distinguant les maisons et les appartements
Une mutation peut contenir plusieurs types de locaux

On conserve chaque couple mutation/disposition qui contient une nature de culture sols ou vide. On suppose que ces mutations concernent des biens à visée d'habitation. Pour ces mutations, on regarde si elles contiennent :
- un local de type 'Maison' :  la transaction est référencée comme une maison
- un local de type 'Appartement' (mais sans 'Maison') : la transaction est référencée comme un appartement
- aucun local de type 'Maison' ou 'Appartement' : la transaction n'est pas retenue

La valeur foncière étant dupliquée, seule sa première occurence est retenue. Le nombre de pièces retenu est le plus grand de toutes les lignes de restitution. Les surfaces réelles sont additionnées par mutation.

On vérifie que toutes les transactions concernent des surfaces non nulles

In [48]:
df_cotieres = df_cotieres.drop_duplicates(subset=['nom'])

In [49]:
df = pd.merge(df, df_cotieres, how='left', left_on='nom_commune', right_on='nom')

In [50]:
# Calcul de la moyenne des prix totale en fonction de la surface
prix_moyen_m2 = df['valeur_fonciere'].sum() / df['surface_reelle_bati'].sum()
print(f"Moyenne totale des prix en fonction de la surface : {prix_moyen_m2:.2f} €")

# Groupement par région et type_local pour calculer les prix moyens
prix_moyen = (
    df.groupby(['regionName', 'type_local'])
    .apply(lambda group: group['valeur_fonciere'].sum() / group['surface_reelle_bati'].sum())
    .reset_index(name='prix_moyen')
)

# Conversion en tableau croisé dynamique (pivot table)
tableau_prix_moyen = prix_moyen.pivot_table(
    index='regionName',
    columns='type_local',
    values='prix_moyen',
    aggfunc='mean'  # Non nécessaire ici car chaque cellule est déjà agrégée
)

# Remplir les valeurs manquantes par 0 ou autre
tableau_prix_moyen = tableau_prix_moyen.fillna(0)

# Calcul du nombre de transactions par région
nb_transactions_region = df.groupby('regionName').size()

# Calcul du pourcentage d'appartements et de maisons par région
nb_transactions_appart = df[df['type_local'] == "Appartement"].groupby('regionName').size()
nb_transactions_maison = df[df['type_local'] == "Maison"].groupby('regionName').size()

# Calculer le pourcentage pour chaque type par région
pourcentage_appart = (nb_transactions_appart / nb_transactions_region * 100).fillna(0)
pourcentage_maison = (nb_transactions_maison / nb_transactions_region * 100).fillna(0)


Moyenne totale des prix en fonction de la surface : 3901.89 €


In [51]:
# Création de la variable adresse_py en remplaçant les espaces par des "+"
df['adresse_py'] = df['Adresse'].str.replace(' ', '+', regex=True)

In [52]:
commune = pd.read_csv('data/communes_code.csv', sep=';',encoding="utf-8")

# Left_join des codes_communes avec les noms des communes geoJson
df = df.merge(commune, left_on=["code_commune"], right_on=['code'], how='left')
df = df.sort_values(by='code_commune', ascending=True)

On souhaite compléter le maximum des transactions qui n'ont pas été géolocalisées précisément dans leur commune.

In [53]:
# Nombre total de transactions renseignées (celles qui ont des valeurs dans 'latitude' et 'longitude')
total_transactions_renseignees = df.shape[0]

# Nombre de lignes où 'latitude' ou 'longitude' est manquant (sans double compte)
non_geolocalisees = df[df['latitude'].isna() | df['longitude'].isna()].shape[0]

# Calcul du pourcentage de transactions non géolocalisées
pourcentage_non_geolocalisees = (non_geolocalisees / total_transactions_renseignees) * 100

# Affichage de la phrase
print(f"Sur les {total_transactions_renseignees} transactions renseignées, {pourcentage_non_geolocalisees:.2f}% ne sont pas géolocalisées.")

Sur les 125887 transactions renseignées, 0.42% ne sont pas géolocalisées.


In [54]:
# Calculer le nombre de transactions par commune
nombre_transactions_cotieres = df.groupby('communeName').size().reset_index(name='Nombre de transactions')

In [55]:
df_missing = df[df['latitude'].isna()]

In [56]:
print(df_missing.value_counts()/df.value_counts*100)

Series([], Name: count, dtype: object)


In [57]:
df_missing = df_missing.drop(columns=['latitude', 'longitude'])

### Complète les coordonnées des ventes manquantes avec l'API Adresse de data.gouv.fr

In [58]:
df_missing = geolocaliser.geolocaliser_actifs(df_missing, 'adresse_py', 'latitude', 'longitude')

### Ajoute les nouvelles coordonnées / Supprime les dernières transactions non localisées

In [59]:
df_missing = df_missing.dropna(subset=['latitude'])
df_final = pd.concat([df, df_missing], ignore_index=True).drop(columns=['departmentCode','communeName','code'])

## 2ème base intermédiaire : Enregistre la base des transactions côtières gélocalisées

In [64]:
df_final['code_departement'] = df_final['code_departement'].astype(str)

In [65]:
df_final.to_parquet("data/base.parquet", index=False,engine='pyarrow')

---
# 5. Localiser les zones inondables
[Retour au sommaire](#sommaire)

### Charge les transactions côtières (2ème base intermédiaire précédente)

In [66]:
# Charger le fichier Parquet contenant les transactions
transactions = pd.read_parquet("data/base.parquet", engine="pyarrow")

On utilise l'API Géorisques (https://georisques.gouv.fr/api/v1/tri_zonage).
Les requêtes étant assez longues, on utilise une méthode de parallélisation (threads simultanés) pour requêter simultanément jusqu'à 5 transactions.

La requête de l'API Géorisques renseigne 4 informatons :
- la présence ou non dans une zone inondable (results)
- si présence, la zone géographique TRI (Territoire à Risque Important d'Inondation) à laquelle le point géographique est associé 
- si présence, le code scénario associé. Il existe 4 scénarios distincts :
    - l'aléa de forte probabilité (01For) dénommé "évènement fréquent" avec une période de retour de 10 à 30 ans
    - l'aléa de moyenne probabilité (02Moy) dénommé "évènement moyen", avec une période d eretour de 100 à 300 ans
    - l'aléa de moyenne probabilité avec changement climatique (03Mcc) dénommé "évènement moyen avec changement climatique" (qui est une majoration d'un évènement moyen)
    - l'aléa de faible probabilité (03Fai), dénommé "évènement extrême" avec une période de retour d'au moins 1000 ans

La période de retour est la durée moyenne au cours de laquelle un évènement d'une même intensité est amené à se reproduire

- si présence, l'aléa d'inondation associé : submersion marine, débordements des cours d'eau, ruissellement et débordements des eaux souterraines

In [67]:
# Préparer les données nécessaires (coordonnées)
coordinates = list(zip(transactions['latitude'], transactions['longitude']))

# Limiter le nombre de threads simultanés pour éviter la surcharge
with ThreadPoolExecutor(max_workers=5) as executor:  # Limite de 5 threads
    results = list(executor.map(request_tri.check_inondable_parallel, coordinates))

# Convertir les résultats en DataFrame
results_df = pd.DataFrame(results, columns=['results', 'identifiant_tri', 'libelle_type_inondation', 'code_scenario'])

# Fusionner les résultats avec les données originales
transactions = pd.concat([transactions.reset_index(drop=True), results_df], axis=1)

On renomme "results" en "zone_inondable" et on la transforme en indicatrice (présence ou non en zone inondable)

In [68]:
# Sauvegarder le fichier avec les résultats
transactions = transactions.rename(columns={'results': 'zone_inondable'})
transactions['zone_inondable'] = transactions['zone_inondable'].replace({2: 0, 3: 0})

### 3ème base intermédiaire : les transactions renseignées sur leur présence en zone inondable

In [69]:
transactions.to_parquet("data/transactions_with_zone_inondable.parquet", index=False, engine="pyarrow")

In [134]:
# Étape 1 : Compter et afficher le nombre de transactions par commune
transaction_counts = transactions.groupby('nom_commune').size().sort_values(ascending=False)
display(transaction_counts)

nom_commune
Nice           7721
Nantes         5049
Bordeaux       4601
Toulon         3075
Cannes         2831
               ... 
Aregno            1
Cagnano           1
Cargèse           1
Mauny             1
Île-de-Batz       1
Length: 946, dtype: int64

On retient les communes qui comptent au moins 10 transactions dont 5 en zones inondables

In [71]:
# Filtrer les transactions pour les Maisons
filtered_maisons = transactions[transactions['type_local'] == 'Maison']
filtered_maisons = filtered_maisons.groupby('nom_commune').filter(
    lambda group: len(group) >= 10 and group['zone_inondable'].sum() > 5 and (group['zone_inondable'] == 0).any()
)

# Filtrer les transactions pour les Appartements
filtered_appartements = transactions[transactions['type_local'] == 'Appartement']
filtered_appartements = filtered_appartements.groupby('nom_commune').filter(
    lambda group: len(group) >= 10 and group['zone_inondable'].sum() > 5 and (group['zone_inondable'] == 0).any()
)

# Combiner les deux sous-ensembles filtrés
filtered_transactions = pd.concat([filtered_maisons, filtered_appartements])


In [72]:
# Étape 3 : Calculer la moyenne agrégée des prix par commune et par zone inondable
filtered_transactions['prix_m2'] = filtered_transactions['valeur_fonciere'] / filtered_transactions['surface_reelle_bati']

In [73]:
# Moyenne par commune et zone inondable
mean_prices = filtered_transactions.groupby(['nom_commune', 'zone_inondable'])['prix_m2'].mean().unstack()

On compare les prix moyens en zone inondable. Pour les appartements, les écarts sont à première vue importants mais ne vont pas dans le même sens selon les communes

In [74]:
# Appeler la fonction mise à jour
appart_table = process_data.produce_stats(filtered_appartements, 'data/moyenne_appartements.csv')

# Afficher le tableau dans le notebook
display(appart_table)

Pour les maisons, on fait un constat similaire. Il n'y a, à première vue, pas de différence marquée, au global entre le prix des maisons en zone inondable et celles en zone non-inondables

In [75]:

# Processus pour les maisons
maison_table = process_data.produce_stats(filtered_maisons, 'data/moyenne_maisons.csv')
display(maison_table)  # Affiche dans le notebook


# 6. Visualisation
[Retour au sommaire](#sommaire)

En préalable, on a récupéré les fichiers shp des Territoires à Risques importants d'Inondation (TRI)
Celles-ci sont trop volumineuses pour être importées directement dans le programme.

In [76]:
# Charger le fichier SHP
gdf = gpd.read_file('data/zones_inondables/zones_inondables.shp')

Les zones inondables sont localisées en système Lambert-93 (coordonnées planes, EPSG 2154)

In [77]:
print(gdf.crs)

EPSG:2154


On les convertit dans le système GPS longitude/latitude (WGS 84, EPSG 4326)

In [78]:
gdf.to_crs(4326, inplace=True)

On repart de la base des transactions côtières (3ème base intermédiaire)

In [79]:
base = pd.read_parquet('data/transactions_with_zone_inondable.parquet',engine='pyarrow')

Certaines villes sont dans une commune côtières mais ne sont pas directement localisées au bord de mer.
Pour éviter ce biais, nous ne retenons que les communes qui ont recensé des transactions dans des zones soumises au risque de submersion marine et où une des zones TRI est présenet.

In [80]:
# Étape 1 : Lister les noms des communes ayant au moins une "submersion marine"
communes_submersion = base.loc[base['libelle_type_inondation'] == "submersion marine", 'nom_commune'].unique()

# Étape 2 : Filtrer le DataFrame pour ne garder que :
# - Les communes ayant une submersion marine
# - Les communes où "identifiant_tri" est renseigné pour au moins une des lignes
base = base[
    base['nom_commune'].isin(communes_submersion) & 
    base.groupby('nom_commune')['identifiant_tri'].transform('any')
]

On présente ici les communes retenues par ce retraitement.

In [81]:
# Supprimer les doublons par 'nom_commune'
commune = base.drop_duplicates(subset='nom_commune')

# Retenir uniquement les colonnes 'nom_commune' et 'Population'
commune = commune[['nom_commune', 'Population']]

# Trier par 'Population' de manière décroissante
commune = commune.sort_values(by='Population', ascending=False)

In [82]:
# Filtrer les valeurs uniques par 'nom_commune' et trier par 'population'
top_100_communes = base.drop_duplicates(subset='nom_commune').nlargest(100, 'Population')

# Afficher un aperçu des 40 plus grandes communes
display(top_100_communes[['nom_commune', 'Population']])


nom_commune  Population
8185                      Nice      348085
51978                 Bordeaux      261804
120229                  Toulon      180452
25617                     Caen      108200
91509                Dunkerque       86788
...                        ...         ...
33707   Saint-Georges-d'Oléron        3948
15                      Fleury        3896
123518        Beauvoir-sur-Mer        3876
38871                  Bénodet        3790
30831                   Arvert        3774

[100 rows x 2 columns]

In [83]:
# Filtrer 'base' pour ne conserver que les communes présentes dans 'top_100_communes'
top_100_communes_names = top_100_communes['nom_commune'].unique()  # Liste des noms de communes les plus peuplées
filtered_base = base[base['nom_commune'].isin(top_100_communes_names)]

# Grouper par 'nom_commune' et 'identifiant_tri', puis compter le nombre d'occurrences
zone_counts = filtered_base.groupby(['nom_commune', 'identifiant_tri']).size().reset_index(name='nombre_occurences')

# Ajouter la population des communes à 'zone_counts' en fusionnant avec 'top_100_communes'
zone_counts = pd.merge(zone_counts, top_100_communes[['nom_commune', 'Population']], on='nom_commune', how='left')

# Trier par population des communes (en ordre décroissant)
tri_by_commune = zone_counts.sort_values(by='Population', ascending=False) \
    .drop(columns=['Population']) \
.reset_index(drop=True)

# Afficher le résultat trié
display(tri_by_commune)

nom_commune                         identifiant_tri  \
0                      Nice                            FRD_TRI_NICE   
1                  Bordeaux                            FRF_TRI_BORD   
2                    Toulon                          FRD_TRI_TOULON   
3                      Caen                            FRH_TRI_CAEN   
4                 Dunkerque                       FRA_TRI_DUNKERQUE   
..                      ...                                     ...   
96   Saint-Georges-d'Oléron            FRFG_TRI_LITTORAL_CHARENTAIS   
97                   Fleury                        FRD_TRI_NARBONNE   
98         Beauvoir-sur-Mer    FRG_TRI_NOIRMOUTIER_ST_JEAN_DE_MONTS   
99                  Bénodet  FRG_TRI_QUIMPER_LITTORAL_SUD_FINISTERE   
100                  Arvert            FRFG_TRI_LITTORAL_CHARENTAIS   

     nombre_occurences  
0                  985  
1                  331  
2                  633  
3                   39  
4                  129  
..                 ...  
96                  13  
97                  71  
98                  19  
99                  13  
100                  1  

[101 rows x 3 columns]

In [84]:
gdf = gdf.drop(columns=['id','dept'])

In [85]:
# Forcer la conversion de la colonne 'beach_coordinates' en liste de tuples (latitude, longitude)
base['beach_coordinates'] = base['beach_coordinates'].apply(mapping.force_convert_to_tuple_list)
base['station'] = base['station'].apply(mapping.force_convert_to_tuple_list)


In [86]:
communes_coordinates = (
    base[['nom_commune',                         
          'latitude_mairie',
          'longitude_mairie',
          'latitude_port',
          'longitude_port',
          'station',
          'beach_coordinates',
          'Population']]
    .drop_duplicates(subset=['nom_commune'], keep='first')  # Supprime les doublons sur 'nom_commune', garde le premier
    .merge(
        tri_by_commune.drop(columns=['nombre_occurences']),  # Retire 'nombre_occurences' avant la jointure
        how='left',
        on='nom_commune'
    )
    .sort_values(by='Population',ascending=False)  # Trie par ordre alphabétique sur 'nom_commune'
)

In [87]:
# mapping.generate_and_save_maps(base, communes_coordinates, gdf)

Un exemple : à Cherbourg-en-Cotentin, le gradient de prix est dirigé autour du port et de la mairie. Les zones inondables ont des prix moyens beaucoup plus faibles

In [88]:
mapping.display_map_in_notebook('Cherbourg-en-Cotentin', base, communes_coordinates, gdf, zoom=13,latitude_add=+0.01,longitude_add=-0.01)

Lorsque la zone inondable est plus large, le gradient de prix est perturbé, mais s'éloigne de la zone.

A Ouistreham, la zone inondable (lié au ruissellement du fleuve) coupe la ville en 2. Le gradient négatif vers cette zone puis positif au delà.

In [89]:
mapping.display_map_in_notebook('Ouistreham', base, communes_coordinates, gdf, zoom=13,latitude_add=0.0,longitude_add=0.00)


A Andernos, les gradients sont très forts auprès des différentes plages, mais deviennent négatifs sur le reste du littoral, qui est inondable.

In [90]:
mapping.display_map_in_notebook('Andernos-les-Bains', base, communes_coordinates, gdf, zoom=13,latitude_add=-0.02,longitude_add=-0.01)


A Agde, le gradient est très fort vers la plage de la Dalle, mais devient négatif aussitôt qu'on s'en éloigne et qu'on se rapproche des zones inondables

In [91]:
test = base[base['nom_commune']=='Cannes']

In [92]:
mapping.display_map_in_notebook('Cannes', base, communes_coordinates, gdf, zoom=14, latitude_add=-0.0, longitude_add=0.0)

In [93]:
# Charger le fichier CSV
df = pd.read_parquet("data/transactions_with_zone_inondable.parquet", engine="pyarrow")

In [94]:
parcelle = pd.read_parquet("data/parcelle_dpe.parquet", engine="pyarrow")

In [95]:
# Effectuer le merge
df2 = pd.merge(
    df, 
    parcelle, 
    how='left', 
    left_on='id_parcelle', 
    right_on='parcelle_id'
)

### 4ème base intermédiaire : le fichier des transactions avec zone inondable, DPE et période de construction

In [96]:
df2.to_parquet('data/transactions_with_inondable_et_dpe.parquet',index=False,engine='pyarrow')

---
# 7. Modele econometrique
[Retour au sommaire](#sommaire)

On repart de la base des transactions en zone inondable et avec caractéristiques hédoniques (4ème base intermédiaire)

In [97]:
transactions = pd.read_parquet("data/transactions_with_inondable_et_dpe.parquet",engine='pyarrow')

In [98]:
# Supposons que 'df' est déjà défini
# Étape 1 : Lister les noms des communes ayant au moins une "submersion marin"
communes_submersion = transactions.loc[transactions['libelle_type_inondation'] == "submersion marine", 'nom_commune'].unique()

# Étape 2 : Filtrer le DataFrame pour ne garder que ces communes
df = transactions[transactions['nom_commune'].isin(communes_submersion)]

In [99]:
# Étape 1 : Filtrer les communes n'ayant pas "submersion marine"
communes_non_submersion = transactions[~transactions['nom_commune'].isin(communes_submersion)][['nom_commune', 'Population']]

# Étape 2 : Supprimer les doublons si nécessaire (par commune) - si tu veux des lignes uniques
communes_non_submersion = communes_non_submersion.drop_duplicates(subset='nom_commune')

# Étape 3 : Trier par population décroissante
communes_non_submersion = communes_non_submersion.sort_values(by='Population', ascending=False).reset_index(drop=True)

# Afficher les 40 premières communes
display(communes_non_submersion.head(10))


nom_commune  Population
0      Nantes      323204
1       Brest      139619
2   Perpignan      119656
3       Rouen      114083
4     Béziers       80341
5     Quimper       63642
6     Lorient       57846
7      Vannes       54420
8     Bayonne       52749
9       Arles       50415

On calcule une indicatrice de présence d'une terrain et d'une dépendance.

In [100]:
df['terrain'] = (df['surface_terrain'] > 0).astype(int)
df['dependance'] = df['dependance'].fillna(False).astype(int)

In [101]:
# Décompte total des transactions par commune
decompte_communes = df['nom_commune'].value_counts()

# Décompte des transactions inondables par commune
decompte_inondables = df[df['zone_inondable'] == 1]['nom_commune'].value_counts()

# Convertir les deux décomptes en DataFrames
decompte_communes_df = decompte_communes.reset_index()
decompte_communes_df.columns = ['nom_commune', 'transactions']

decompte_inondables_df = decompte_inondables.reset_index()
decompte_inondables_df.columns = ['nom_commune', 'transactions_inondables']

# Fusionner les deux DataFrames sur le nom de la commune
decompte_final = pd.merge(decompte_communes_df, decompte_inondables_df, on='nom_commune', how='left')

# Remplacer les valeurs NaN par 0 (communes sans transactions inondables)
decompte_final['transactions_inondables'] = decompte_final['transactions_inondables'].fillna(0).astype(int)

# Fusionner avec le DataFrame initial pour conserver les autres colonnes de `df` (optionnel)
df = pd.merge(df, decompte_final, on='nom_commune', how='left')


On fait un modèle géographique : on calcule, pour chaque transaction, la distance aux lieux géographiques (mairie, plage, station).

Pour la liste des plages (qui inclut également le port) et des stations, on calcule les distances de l'actif à chaque lieu et on retient la distance la plus courte.

In [102]:
# D'abord les mairies (assimilées au centre-ville)
df['distance_centre_ville'] = df.apply(
    lambda row: modeling.distance_haversine(
        row['latitude'], row['longitude'],
        row['latitude_mairie'], row['longitude_mairie']
    ),
    axis=1
)

In [105]:
# Puis les plages et les stations : on convertit d'abord les chaînes en listes de tuples
df["beach_coordinates"] = df["beach_coordinates"].apply(
    lambda x: ast.literal_eval(x) if isinstance(x, str) else x
    )

df["station"] = df["station"].apply(
    lambda x: ast.literal_eval(x) if isinstance(x, str) else x
    )

In [106]:
df["beach_coordinates"] = df["beach_coordinates"].apply(modeling.nettoyer_coordinates)
df["station"] = df["station"].apply(modeling.nettoyer_coordinates)

In [107]:
# Calcul de la distance minimale à la plage ou au port en fonction de la disponibilité des données
df["distance_min_beach"] = df.apply(
    lambda row: modeling.distance_minimale(row["latitude"], row["longitude"], row["beach_coordinates"])
    if row["beach_coordinates"] else None,  # Si aucune coordonnée plage disponible, retourner None
    axis=1
)

# Si distance_min_beach est NaN, calculer la distance au port
df["distance_min_beach"] = df.apply(
    lambda row: modeling.distance_haversine(
        row['latitude'], row['longitude'],
        row['latitude_port'], row['longitude_port']
    ) if pd.isna(row["distance_min_beach"]) else row["distance_min_beach"],
    axis=1
)

In [108]:
# Puis les stations

df["distance_min_station"] = df.apply(
    lambda row: modeling.distance_minimale(row["latitude"], row["longitude"], row["station"])
    if row["station"] else None,  # Si aucune coordonnée disponible, retourner None
    axis=1
)

On prépare le reste des variables pour la régression :
- la taille de la commune (3 catégories : 10 000, 10 à 20 000, 20 000 et +)
- le type d'aléa (faible, moyen ou fort) pour les transactions en zone inondable


In [110]:
### Taille de la commune

bins = [0, 10000, 20000, np.inf]  # bornes des tranches
labels = ['0-10000','10000-20000','plus_20000']  # Labels des tranches
df['pop_cut'] = pd.cut(df['Population'], bins=bins, labels=labels, right=False)
df_dummies_population = pd.get_dummies(df['pop_cut'], prefix='population',drop_first=True)
df_dummies_population = df_dummies_population.astype(int)

In [111]:
### Niveau de gravité de l'aléa

df['code_scenario'] = df['code_scenario'].replace({
    '02Moy': '02Moy_03Mcc',
    '03Mcc': '02Moy_03Mcc'
})

df_dummies_scenario = pd.get_dummies(df['code_scenario'], prefix='scenario').astype(int)

In [112]:
display(df['code_scenario'].value_counts(dropna=False))

code_scenario
None           49667
02Moy_03Mcc     4550
04Fai           3284
01For           1271
Name: count, dtype: int64

Les variables suivantes sont des indicatrices. Après les avoir transformées, on retire une des modalités afin d'éviter la présence de multicolinéarité dans la régression (par exemple : $\sum_{j communes}I(i \in commune)) = 1$ car chaque transaction est forcément dans une commune

On supprime, en général, la référence qui contient le plus de transactions (ex : Nice pour les communes) et/ou celle qui permet d'observer un effet graduel des catégories (ex : si les DPE E-F-G sont la référence, on s'attend à observer des effets sur les prix plus élevés pour les indicatrices en D, C, B, A)

In [113]:
### Année de construction de l'habitation

df['periode_construction_dpe'] = df['periode_construction_dpe'].replace({
    '2013-2021': 'après 2013',
    'après 2021': 'après 2013',
    '2001-2005': '2001-2012',
    '2006-2012': '2001-2012',
    '1983-1988': '1975-1988',
    '1978-1982': '1975-1988',
    '1975-1977': '1975-1988'
})

# Création des dummies pour la colonne 'periode_construction_dpe'
df_dummies_construction = pd.get_dummies(df['periode_construction_dpe'], prefix='periode_construction_dpe')
df_dummies_construction = df_dummies_construction.drop(columns=['periode_construction_dpe_avant 1948'], errors='ignore')
df_dummies_construction = df_dummies_construction.astype(int)

In [114]:
### Classe de DPE (Diagnpostic de performance énergétique) de l'habitation

df_dummies_dpe = pd.get_dummies(df['classe_bilan_dpe'], prefix='dpe')
df_dummies_dpe['dpe_E_F_G'] = df_dummies_dpe['dpe_G'] | df_dummies_dpe['dpe_F'] | df_dummies_dpe['dpe_E']

df_dummies_dpe = df_dummies_dpe.drop(columns=['dpe_G', 'dpe_F','dpe_E'])
df_dummies_dpe = df_dummies_dpe.drop(columns=['dpe_E_F_G'], errors='ignore')
df_dummies_dpe = df_dummies_dpe.astype(int)

In [133]:
df=df.dropna(subset=['periode_construction_dpe'])

# Vérifier le résultat final
display(df.iloc[:, 1:].head())

id_mutation  numero_disposition  valeur_fonciere  surface_reelle_bati  \
1  2023-77223                 1.0          95000.0                 37.0   
2  2023-72369                 1.0         371800.0                 54.0   
4  2023-72366                 1.0         261000.0                 37.0   
5  2023-72365                 1.0         215000.0                 59.0   
6  2023-64103                 1.0         650000.0                130.0   

   surface_terrain  nombre_locaux  dependance  nombre_pieces_principales  \
1              0.0            1.0         0.0                        2.0   
2              0.0            3.0         1.0                        2.0   
4              0.0            3.0         1.0                        1.0   
5              0.0            2.0         1.0                        3.0   
6              0.0            3.0         1.0                        3.0   

  date_mutation adresse_numero  ... dpe_B dpe_C dpe_D debordement  \
1    2023-12-11             30  ...     0     0     0           0   
2    2023-08-25             33  ...     0     0     0           0   
4    2023-08-31             14  ...     0     1     0           0   
5    2023-08-25             16  ...     0     0     1           0   
6    2023-03-21             12  ...     0     0     1           0   

  zone_inondable x debordement log_surface_reelle_bati log_prix_m2  \
1                          0.0                3.610918    7.850714   
2                          0.0                3.988984    8.837127   
4                          0.0                3.610918    8.861358   
5                          0.0                4.077537    8.200856   
6                          0.0                4.867534    8.517193   

   log_distance_min_beach  log_distance_min_station log_distance_centre_ville  
1                1.140956                 -0.415447                  0.465779  
2                0.736207                 -0.471093                 -0.172764  
4                0.949676                 -1.478212                 -1.185755  
5                1.087827                 -0.195294                  0.175752  
6                1.082647                 -0.209567                  0.279660  

[5 rows x 235 columns]

In [116]:
### Indicatrices de présence dans chaque commune

colonnes_a_conserver = [col for col in df.columns if not col.startswith('commune_')]

df = df[colonnes_a_conserver]

# Création des dummies pour les communes
df_dummies_communes = pd.get_dummies(df['nom_commune'], prefix='commune')
df_dummies_communes = df_dummies_communes.drop(columns=['commune_Nice'])
df_dummies_communes = df_dummies_communes.astype(int)

On ajoute toutes les indicatrices au dataframe.

In [117]:
df = pd.concat([df,
                df_dummies_population,
                df_dummies_scenario,
                df_dummies_communes,
                df_dummies_construction,
                df_dummies_dpe
                ],
               axis=1
               )

La variable d'interaction (zone inondable x debordement) est un produit d'indicatrice qui calcule, en présence de la variable zone_inondable, l'effet relatif d'être en zone de débordement par rapport au fait d'être en zone de submersion marine.

In [118]:
df['debordement'] = (df['libelle_type_inondation'] == "débordement de cours d'eau").astype(int)
df['zone_inondable x debordement'] = df['zone_inondable'] * df['debordement']

On passe en log les variables quantitatives continues

In [119]:
# Transformation en log de certaines colonnes
variables_continues =    ["surface_reelle_bati",
                          "prix_m2",
                          "distance_min_beach",
                          "distance_min_station",
                          "distance_centre_ville"
                          ]

df = modeling.transformer_log(df, variables_continues)

On définit les variables spatiales et les 4 ensembles de variables explicatives associées à 4 modèles de régression.
Chaque ensemble de variables explicatives introduit des variables supplémentaires par rapport au bloc précédent. Cela permettra de mesurer l'effet de cet ajout, et en particulier l'effet sur le coefficient d'intérêt (celui de la zone inondable)

In [120]:
colonnes_geographiques = [
    "log_distance_min_beach",
    "log_distance_min_station",
    "log_distance_centre_ville"
]

colonnes_explicatives = [
    "zone_inondable",
    "log_surface_reelle_bati",
    "nombre_pieces_principales",
    'dependance',
    'terrain'
] + [
    col for col in df.columns if col.startswith('population')
] + [
    col for col in df.columns if col.startswith('dpe')
] + [
    col for col in df.columns if col.startswith('periode_construction_dpe_')
]

colonnes_explicatives1 = colonnes_explicatives + [col for col in df.columns if col.startswith('commune_')]

colonnes_explicatives2 = colonnes_explicatives1 + colonnes_geographiques

colonnes_explicatives3 = [
    col for col in colonnes_explicatives2 if col != "zone_inondable"
] + [
    col for col in df.columns if col.startswith("scenario")
    ]
    
colonnes_explicatives4 = colonnes_explicatives2 + ['zone_inondable x debordement']

colonne_dependante = "log_prix_m2"

On crée 4 modèles de régression pour les appartements
- le 1er modèle intègre seulement les variables hédoniques, et l'indicatrice en zone inondable
- le 2ème modèle ajoute les variables géographiques, dont la distance à la plage
- le 3ème modèle remplace l'indicatrice de zone par 3 indicatrices par aléa (risque faible, moyen, fort)
- le 4ème modèle intègre la variable d'interaction (zone_inondable x débordement) pour différencier le risque marin du risque fluvial

$$
\begin{align*}
\text{Modèle 1:} & \quad \log(y_i) = \alpha_0 + \alpha_1 \, I(i \in \text{zone inondable}) + \sum_{k \in \text{hédoniques}} \gamma_k \, h_{ik}  + \sum_{j \in \text{communes}} \delta_j \, I(i \in \text{commune } j) + \varepsilon \\
\text{Modèle 2:} & \quad \log(y_i) = \alpha_0 + \alpha_1 \, I(i \in \text{zone inondable}) + \sum_{k \in \text{géographiques}} \beta_k \, g_{ik} + \sum_{k \in \text{hédoniques}} \gamma_k \, h_{ik} + \sum_{j \in \text{communes}} \delta_j \, (i \in \text{commune } j) + \varepsilon \\
\text{Modèle 3:} & \quad \log(y_i) = \alpha_0 + \alpha_1 \, I(i \in \text{risque faible}) + \alpha_2 \, I(i \in \text{risque moyen}) + \alpha_3 \, I(i \in \text{risque fort}) + \sum_{k \in \text{géographiques}} \beta_k \, g_{ik} + \sum_{k \in \text{hédoniques}} \gamma_k \, h_{ik} + \sum_{j \in \text{communes}} \delta_j \, I(i \in \text{commune } j) + \varepsilon \\
\text{Modèle 4:} & \quad \log(y_i) = \alpha_0 + \alpha_1 \, I(i \in \text{zone inondable}) + \alpha_2 \, I(i \in \text{zone inondable x débordement}) + \sum_{k \in \text{géographiques}} \beta_k \, g_k + \sum_{k \in \text{hédoniques}} \gamma_k \, h_{ik} + \sum_{j \in \text{communes}} \delta_j \, I(i \in \text{commune } j) + \varepsilon
\end{align*}
$$


### Description des variables

- $y$ : Variable dépendante, log-transformée.
- $\alpha_0$ : Constante ou intercept du modèle.
- $\alpha_1, \alpha_2, \alpha_3$ : Coefficients associés aux indicateurs des différentes catégories, comme le risque faible, moyen ou fort, ou la zone inondable.
- $I(i \in \text{catégorie})$ : Indicatrice, vaut $1$ si l'observation $i$ appartient à la catégorie spécifiée, sinon $0$.
- $h_k$ : Variables explicatives hédoniques, comme la surface, le nombre de pièces principales, etc.
- $g_k$ : Variables explicatives géographiques, comme la distance au centre-ville ou la proximité des plages.
- $\gamma_k$ : Coefficients associés aux variables hédoniques.
- $\beta_k$ : Coefficients associés aux variables géographiques.
- $\delta_j$ : Effets fixes spécifiques à la commune $j$.
- $\varepsilon$ : Terme d'erreur aléatoire.

On estime les coefficients par la méthode des moindres carrés ordinaires (MCO) d'abord pour les appartements.

In [121]:
df_app = df[df["type_local"]=="Appartement"]

model_app1 = modeling.construire_modele_regression(
    df_app,
    colonnes_explicatives=colonnes_explicatives1,
    colonne_dependante=colonne_dependante
)

model_app2 = modeling.construire_modele_regression(
    df_app,
    colonnes_explicatives=colonnes_explicatives2,
    colonne_dependante=colonne_dependante
)

model_app3 = modeling.construire_modele_regression(
    df_app,
    colonnes_explicatives=colonnes_explicatives3,
    colonne_dependante=colonne_dependante
)

model_app4 = modeling.construire_modele_regression(
    df_app,
    colonnes_explicatives=colonnes_explicatives4,
    colonne_dependante=colonne_dependante
)

On procède de même pour les maisons.

In [122]:
df_mai = df[df["type_local"]=="Maison"]

model_mai1 = modeling.construire_modele_regression(
    df_mai,
    colonnes_explicatives=colonnes_explicatives1,
    colonne_dependante=colonne_dependante
)

model_mai2 = modeling.construire_modele_regression(
    df_mai,
    colonnes_explicatives=colonnes_explicatives2,
    colonne_dependante=colonne_dependante
)

model_mai3 = modeling.construire_modele_regression(
    df_mai,
    colonnes_explicatives=colonnes_explicatives3,
    colonne_dependante=colonne_dependante
)

model_mai4 = modeling.construire_modele_regression(
    df_mai,
    colonnes_explicatives=colonnes_explicatives4,
    colonne_dependante=colonne_dependante
)


In [123]:
# Extraction des résultats pour les modèles appartements
resultats_app1 = modeling.extraire_resultats_modele(model_app1, "A.1")
resultats_app2 = modeling.extraire_resultats_modele(model_app2, "A.2")
resultats_app3 = modeling.extraire_resultats_modele(model_app3, "A.3")
resultats_app4 = modeling.extraire_resultats_modele(model_app4, "A.4")

# Extraction des résultats pour les modèles maisons
resultats_mai1 = modeling.extraire_resultats_modele(model_mai1, "M.1")
resultats_mai2 = modeling.extraire_resultats_modele(model_mai2, "M.2")
resultats_mai3 = modeling.extraire_resultats_modele(model_mai3, "M.3")
resultats_mai4 = modeling.extraire_resultats_modele(model_mai4, "M.4")

In [124]:
# Retire les coefficients associés aux communes pour davantage de lisibilité
resultats_app1 = modeling.filtrer_variables(resultats_app1)
resultats_app2 = modeling.filtrer_variables(resultats_app2)
resultats_app3 = modeling.filtrer_variables(resultats_app3)
resultats_app4 = modeling.filtrer_variables(resultats_app4)

resultats_mai1 = modeling.filtrer_variables(resultats_mai1)
resultats_mai2 = modeling.filtrer_variables(resultats_mai2)
resultats_mai3 = modeling.filtrer_variables(resultats_mai3)
resultats_mai4 = modeling.filtrer_variables(resultats_mai4)

In [125]:
# Effectuer les jointures sur la colonne 'variable' pour les appartements puis les maisons
tableau_app = resultats_app1.merge(resultats_app2, on="variable", how="outer")
tableau_app = tableau_app.merge(resultats_app3, on="variable", how="outer")
tableau_app = tableau_app.merge(resultats_app4, on="variable", how="outer")

tableau_mai = resultats_mai1.merge(resultats_mai2, on="variable", how="outer")
tableau_mai = tableau_mai.merge(resultats_mai3, on="variable", how="outer")
tableau_mai = tableau_mai.merge(resultats_mai4, on="variable", how="outer")

coef_columns_app = [col for col in tableau_app.columns if "_coef" in col]
coef_columns_mai = [col for col in tableau_mai.columns if "_coef" in col]

# Convertir en float et arrondir
tableau_app[coef_columns_app] = tableau_app[coef_columns_app].apply(pd.to_numeric, errors='coerce')
tableau_mai[coef_columns_mai] = tableau_mai[coef_columns_mai].apply(pd.to_numeric, errors='coerce')

# Appliquer l'arrondi et les étoiles aux p-values
model_ids_app = [col.split("_")[0] for col in tableau_app.columns if "_pvalue" in col]
model_ids_mai = [col.split("_")[0] for col in tableau_mai.columns if "_pvalue" in col]

tableau_app = modeling.arrondir_pvalue_ajouter_etoiles(tableau_app, model_ids_app)
tableau_mai = modeling.arrondir_pvalue_ajouter_etoiles(tableau_mai, model_ids_mai)

On réordonne le tableau de régression selon un ordre de variables défini (sans afficher les coefficients associés aux indicatrices de commune)

In [126]:
# Accès aux vecteurs
ordre_variables_app = modeling.ordre_variables_app
ordre_variables_mai = modeling.ordre_variables_mai

# Réorganiser les lignes pour les deux tableaux (app et mai)
tableau_app = modeling.reordonner_lignes(tableau_app, ordre_variables_app)
tableau_mai = modeling.reordonner_lignes(tableau_mai, ordre_variables_mai)

# Appliquer le renommage des colonnes pour chaque tableau
tableau_app = modeling.renommer_coef_colonnes(tableau_app, "App")
tableau_mai = modeling.renommer_coef_colonnes(tableau_mai, "Maison")

Les coefficients des modèles sont estimés ci-dessous, ainsi que le R2 ajusté (indicateur de l'adéquation des données au modèle).

Les pvalues sont présentée, avec les seuils classiques de significativité (* si pvalue < 10%, ** si < 5%, *** si < 1% )

In [127]:
tableau_app.fillna("").style.hide(axis="index")

Interprétation : Comme la variable dépendante (les prix) sont en logarithme, les coefficients estimés peuvent être traduits de la manière suivante :
- si ce sont des indicatrices (ex : la présence en zone inondable), le coefficient est une **semi-élasticité**. Si la variable indicatrice passe de 0 à 1, la variation du log(prix) est $\alpha_1$, et le prix augmente de $100 * \alpha_1 %$


Cette variation peut être interprétée comme une variation en pourcentage du prix, c'est-à-dire :
Variation en pourcentage ≈ $\alpha_1 × 100$

*Exemple : dans le modèle 2, être en zone inondable diminue, toutes choses égales par ailleurs, le prix de 100 * 0.058500 % = 5.9%*

- si ce sont des logarithmes (ex : distance à la plage la plus proche), le coefficient est une **élasticité**. Si la distance augmente de 1%, log(distance) augmente de 1/100, la variation du log(prix) est $\alpha_1/100$, et le prix augmente de $\alpha_1 %$

*Exemple : dans le modèle 2, s'éloigner de 1% de la plage diminue, toutes choses égales par ailleurs, le prix de -0.063 %*

*Note sur l'effet d'interaction* (M4)_ : si le bien est en zone inondable "marin", debordement = 0 et l'effet est capté par la variable $\alpha_1 = 5.7\%$. Si debordement = 1, l'effet inondable est capté par $\alpha_1 + \alpha_2 = 6.7\% - 22.2 \% = -15.5\%$

In [128]:
tableau_mai.fillna("").style.hide(axis="index")

# 6. Conclusion

Notre modèle (hédonique et spatial) est concluant et soutient qu'il existe une décote "climatique" d'environ 6% en moyenne pour les transactions d'appartement en zone inondable. Ce coefficient est sensiblement réhaussé une fois prise en compte la position de l'appartement dans la commune, notamment sa distance aux plages et aux zones touristiques. Les ménages sont donc bien rebutés par la présence en zone inondable, mais la proximité des lieux de loisirs et de vacances compense cette prise de risque, ce qui amoindrit le discount à l'achat.

Pour les maisons, aucun effet significatif n'est mesuré. Cela pourrait s'expliquer par le profil différent des acheteurs : les appartements sont souvent la cible des investisseurs pour la location saisonnière (et ceux-ci privilégient le long terme et anticipent la revente et les pertes associées) tandis que les maisons sont davantage prisées par les particuliers, qui semblent davantage court-termistes et soumis à un effet de "myopie" (ce qui est également confirmé par l'étude de l'INRAE).

Pour les appartements, l'effet n'est pas différent selon la gravité de l'aléa (faible, moyen ou fort ): la seule indication de la zone inondable semble avoir le même effet rebuteur pour tous les acquéreurs. Toutefois, l'effet est sensiblement plus élevé pour le seul risque de débordement de cours d'eau (-22%). Le risque marin peut apparaître beaucoup moins fréquent (du fait de la rareté des tempêtes, dont la dernière d'importance remonte à Xynthia en 2010), tandis que le risque fluvial dans les embouchures est davantage associé à de fortes précipitations et leurs conséquences sont peut-être plus sensibles pour les riverains.

L'effet de myopie semble donc être confirmé : tant que les Français ne mesurent pas directement les conséquences du changement climatique, ils ne se projettent pas (assez ?) sur les problèmes à venir.